# Text to Text  Explanation: Abstractive Summarization Example

This notebook demonstrates use of generating model explanations for a text to text scenario on a pretrained transformer model. Below we demonstrate the process of generating explanations for a pretrained model distilbart on the Extreme Summarization (XSum) Dataset provided by hugging face (https://huggingface.co/sshleifer/distilbart-xsum-12-6). 

The first example only needs the model and tokenizer and we use the model decoder to generate log odds of the output tokens to be explained. In the second example, we demonstrate the use of how to generate expplanations for model in the form of an api/fucntion (input->text and output->text). In this case we need to approximate the log odds by using a text similarity model. The underlying explainer used to compute the shap values is the partition explainer.

In [1]:
import numpy as np
from transformers import AutoTokenizer, AutoModelForSeq2SeqLM
import torch
import nlp
import shap
from shap.models import TeacherForcingLogits
from shap import maskers

### Load model and tokenizer

In [2]:
tokenizer = AutoTokenizer.from_pretrained("sshleifer/distilbart-xsum-12-6")
model =  AutoModelForSeq2SeqLM.from_pretrained("sshleifer/distilbart-xsum-12-6").cuda()

### Load data

In [3]:
dataset = nlp.load_dataset('xsum',split='train')

WARNING - Using custom data configuration default


### Create an explainer object

In [4]:
explainer = shap.Explainer(model,tokenizer)

explainers.Partition is still in an alpha state, so use with caution...


### Compute shap values

In [5]:
shap_values = explainer(dataset['document'][0:1])

### Visualize shap explanations

In [6]:
shap.plots.text(shap_values[0])

### API

Below we demonstrate generating explanations for a model which is an api/function. Since this is a model agnostic case, we use a text similarity model to approximate log odds of generating output text which is used for computing shap explanations.

In [7]:
# Define function
def f(x):
    model.eval()
    input_ids = torch.tensor([tokenizer.encode(x)]).cuda()
    with torch.no_grad():
        out=model.generate(input_ids)
    sentence = [tokenizer.decode(g, skip_special_tokens=True) for g in out][0]
    del input_ids, out
    return sentence

For a model agnostic case, we wrap the model to be explained with the TeacherForcingLogits class and define the text similarrity model and tokenizer. The TeacherForcingLogits class uses the text similarity model to approximate the log odds of generating the output text from the model(function->f)

We also have to create a Text masker and define mask_token="<infill>" which then cues the algorithm to use text infilling while masking

In [8]:
# wrap model with TeacherForcingLogits class
wrapped_model = TeacherForcingLogits(f,text_similarity_model=model, text_similarity_tokenizer=tokenizer, device='cuda')
# create a Text masker
masker = maskers.Text(tokenizer, mask_token = "<infill>")

### Create an explainer object using wrapped model and Text masker

In [9]:
explainer_model_agnostic = shap.Explainer(wrapped_model,masker)

explainers.Partition is still in an alpha state, so use with caution...


### Compute shap values

In [10]:
shap_values_model_agnostic = explainer_model_agnostic(dataset['document'][0:1])

Partition explainer: 2it [00:48, 24.46s/it]                                                                            


### Visualize shap explanations

In [11]:
shap.plots.text(shap_values_model_agnostic[0])